In [4]:
import tensorflow as tf
from tensorflow.keras.layers import Dense, BatchNormalization, Flatten
from tensorflow.keras.callbacks import Callback
from tensorflow.keras.models import Sequential
import tensorflow_model_optimization as tfmot
import numpy as np

import pickle

import rpy2.robjects as robjects
from rpy2.robjects.packages import importr
from rpy2.robjects import FloatVector
import os



In [5]:
# os.environ['R_HOME'] = 'C:\Program Files\R\R-4.1.0' #path R installation


In [6]:
itses = importr('itses') # For SparseMAD() as itses()
est_iterative = robjects.r['itses']

In [7]:

class SureMaskedDense(Dense, tfmot.sparsity.keras.PrunableLayer):
    def __init__(self, units, **kwargs):
        super(SureMaskedDense, self).__init__(units, **kwargs)
        self.units = units
        self.masks = []


    def build(self, input_shape):
        super(SureMaskedDense, self).build(input_shape)
        
        for weight in self.get_prunable_weights():
            self.masks += [tf.Variable(tf.ones(weight.shape, tf.float32),
                                       trainable=False,
                                       name="kernel_mask")]

    def call(self, inputs):
        self.mask_weights()
        return super(SureMaskedDense, self).call(inputs)

    def mask_weights(self):
        for mask, weight in zip(self.masks, self.get_prunable_weights()):
            weight.assign(tf.squeeze(weight * mask))

    def get_prunable_weights(self):
        return [self.kernel]




def hard_threshold(weight, mask, sparsity):
    weights_r = tf.reshape(weight, [-1]).numpy()
    sparsity = sparsity[1].numpy()
    upper_percentile = np.percentile(np.abs(weights_r), sparsity*100)
    print("Wanted sparsity", sparsity)
    print("Upper percentile", upper_percentile)
    try:
        weights_r = FloatVector(weights_r)
        sparsity = FloatVector([sparsity])
        current_threshold = est_iterative(weights_r, method="HT", sparsity=sparsity)[0][0]
        print("Thresholhold", current_threshold)
        old_mask = False
        if(upper_percentile < current_threshold):
            print("Threshold over percentile. Lowering.")
            current_threshold = upper_percentile
        else:
            print("Using suggest threshold.")
    except:
        print("Keeping old")
        old_mask = True

    weight = mask * weight
    if not old_mask:
        print("Applying new mask")
        abs_weight = tf.math.abs(weight)
        new_mask = tf.logical_not(tf.math.greater_equal(abs_weight, current_threshold))
        mask = tf.cast(1. - mask, tf.bool)
        mask = tf.cast(tf.logical_not(tf.math.logical_or(mask, new_mask)), weight.dtype)
        print("Percentage zeros", tf.math.reduce_mean(1. - mask).numpy())
        print(mask)
        weight = weight * mask
    return weight, mask

class ShrinkCallback(Callback):
    def __init__(self, schedule, gradient_adjusment=False, data = None):
        super(ShrinkCallback, self).__init__()
        self.schedule = schedule
        self.gradient_adjusment = gradient_adjusment
        self.steps = 0
        self.data = data

    def prune(self, epoch, weights, masks, tape=None, loss=None, epsilon=1e-12):
        new_masks = []
        sparsity = self.schedule(epoch)

        for weight, mask in zip(weights, masks):
            if self.gradient_adjusment:
                grad = tape.gradient(loss, weight)
                weight = weight / (tf.math.abs(grad) + epsilon)
                new_weight, mask = hard_threshold(weight, mask, sparsity=sparsity)
                new_weight = new_weight * (tf.math.abs(grad) + epsilon)
            else:
                new_weight, mask = hard_threshold(weight, mask, sparsity=sparsity)
            weight.assign(new_weight)
            new_masks += [mask]
        return new_masks
    
    def on_train_begin(self, logs = None):
        self.steps = 0

    def on_batch_begin(self, batch, logs=None):
        self.steps += 1
        if self.schedule(self.steps)[0]:  
            if self.gradient_adjusment:
                for batch in self.data.take(1):
                    x = batch[0]
                    y = batch[1]
                with tf.GradientTape(persistent=True) as tape:
                    y_pred = self.model(x)
                    loss = self.model.loss(y, y_pred)
            else:                
                tape = None
                loss = None



            for layer in self.model.layers:
                if hasattr(layer, 'masks'):
                    layer.mask_weights()
                    weights = layer.get_prunable_weights()
                    new_masks = self.prune(self.steps, weights, layer.masks, tape=tape, loss=loss)

                    for new_mask, old_mask in zip(new_masks, layer.masks):
                        old_mask.assign(new_mask)
                    layer.mask_weights()

            if self.gradient_adjusment:
                del tape
        return
    

    
class SparsityCallback(Callback):
    def get_sparsity(self):
        weights_list = []
        for layer in self.model.layers:
            if isinstance(layer, tf.keras.layers.Wrapper):
                layer = layer.layer
            if isinstance(layer, tfmot.sparsity.keras.PrunableLayer):
                weights = layer.get_prunable_weights()
                weights_list += [tf.reshape(weight,-1).numpy() for weight in weights]
        weights_list = np.concatenate(weights_list)
        print(weights_list)
        return np.mean(weights_list == 0)
    def on_epoch_end(self, epoch, logs = None):
        sparsity = self.get_sparsity()
        logs["sparsity"] = sparsity
        print("Sparsity at:", sparsity)
      
    
def get_data(batch_size, buffer_size = 64):
    (x_train, y_train), (x_test, y_test)  = tf.keras.datasets.mnist.load_data()

    train_dataset = tf.data.Dataset.from_tensor_slices((x_train, y_train))
    test_dataset = tf.data.Dataset.from_tensor_slices((x_test, y_test))

    def mapper(x_train, y_train):
        x_train = tf.cast(x_train, tf.float32)
        y_train = tf.cast(y_train, tf.int32)
        x_train = x_train/255.
        return x_train, y_train
    train_dataset = train_dataset.map(mapper).shuffle(buffer_size).batch(batch_size)
    test_dataset = test_dataset.map(mapper).shuffle(buffer_size).batch(batch_size)

    return train_dataset, test_dataset


def get_mnist_model(kernel_regularizer = 'l2', batch_norm = True):
    if  batch_norm:
        mnist_model = Sequential([
            Flatten(input_shape = (28, 28)),
            SureMaskedDense(300, activation = "relu",kernel_regularizer=kernel_regularizer),
            BatchNormalization(),
            SureMaskedDense(100, activation = "relu",kernel_regularizer=kernel_regularizer),
            BatchNormalization(),
            SureMaskedDense(10, activation = "softmax",kernel_regularizer=kernel_regularizer)])
    else:
        mnist_model = Sequential([
            Flatten(input_shape = (28, 28)),
            SureMaskedDense(64, activation = "tanh",kernel_regularizer=kernel_regularizer),
            SureMaskedDense(128, activation = "tanh",kernel_regularizer=kernel_regularizer),
            SureMaskedDense(10, activation = "softmax",kernel_regularizer=kernel_regularizer)])

    return mnist_model
        
def compile_model(model):
    model.compile(loss=tf.keras.losses.SparseCategoricalCrossentropy(),
                        optimizer=tf.keras.optimizers.Adam(0.001),
                        metrics=['accuracy'])




In [11]:
# Train base
epochs = 200
batch_size = 256
train_dataset, test_dataset = get_data(batch_size)
num_batches = len(list(train_dataset))
end_pruning_epoch =  450
pruning_epoch_frequency = 50
prune_epochs = 500
schedule = tfmot.sparsity.keras.PolynomialDecay(initial_sparsity=0.50,
                                                               final_sparsity=0.99,
                                                               begin_step=1,
                                                               end_step= num_batches * end_pruning_epoch, 
                                                frequency = num_batches*pruning_epoch_frequency)

In [12]:


def get_base_model(epochs,batch_size, train_dataset, test_dataset, kernel_regularizer, batch_norm, seed = 1234):
    tf.random.set_seed(seed)
    mnist_model = get_mnist_model(kernel_regularizer = kernel_regularizer, batch_norm = batch_norm)
    compile_model(mnist_model)
    mnist_model.fit(train_dataset, epochs = epochs, validation_data = test_dataset)
    
    return mnist_model

def iterative_pruning(prune_epcochs, train_dataset, test_dataset, schedule, original_model, seed = 1234):
    iterative_mnist_model = tf.keras.models.clone_model(original_model)
    compile_model(iterative_mnist_model)
    sparsity_callback = SparsityCallback()
    shrink_callback = ShrinkCallback(schedule)
    tf.random.set_seed(seed)
    history_iterative_prune = iterative_mnist_model.fit(train_dataset,
                                                      epochs = prune_epcochs,
                                                      validation_data = test_dataset,
                                                      callbacks = [shrink_callback, sparsity_callback])
    return iterative_mnist_model, history_iterative_prune


def apply_pruning_to_dense(layer, pruning_schedule = schedule):
    if isinstance(layer, tf.keras.layers.Dense):
        return tfmot.sparsity.keras.prune_low_magnitude(layer, pruning_schedule = pruning_schedule)
    return layer

def magnitude_pruning(prune_epcochs, train_dataset, test_dataset, schedule, original_model, seed = 1234):
    tf.random.set_seed(seed)
    magnitude_mnist_model = tf.keras.models.clone_model(
        original_model,
        clone_function=apply_pruning_to_dense,
    )
    compile_model(magnitude_mnist_model)
    sparsity_callback = SparsityCallback()


    callbacks = [
      tfmot.sparsity.keras.UpdatePruningStep(),
        sparsity_callback
    ]
    history_magnitude_prune = magnitude_mnist_model.fit(train_dataset,
                                                      epochs = prune_epcochs,
                                                      validation_data = test_dataset,
                                                      callbacks = callbacks)
    return magnitude_mnist_model, history_magnitude_prune


In [13]:
for j in [1,2,3,4,5]:    
    l2_base_batch = get_base_model(epochs,batch_size, train_dataset, test_dataset, "l2", batch_norm  = True, seed = j)
    base_batch = get_base_model(epochs,batch_size, train_dataset, test_dataset, None, batch_norm  = True, seed = j)

    l2_base_no_batch = get_base_model(epochs,batch_size, train_dataset, test_dataset, "l2", batch_norm  = False, seed = j)
    base_no_batch = get_base_model(epochs,batch_size, train_dataset, test_dataset, None, batch_norm  = False, seed = j)

    models = [l2_base_batch, base_batch, l2_base_no_batch, base_no_batch]

    iterative_histories = []
    iterative_models = []
    for model in models: 
        model, history =  iterative_pruning(prune_epochs, train_dataset, test_dataset, schedule, model, seed = j)
        iterative_models += [model]
        iterative_histories += [history.history]

        with open('output/neural-network-pruning/pickle-jar/iterative_histories'+str(j)+'.pickle', 'wb') as file:
            pickle.dump(iterative_histories, file)

    magnitude_histories = []
    magnitude_models = []
    for model in models: 
        model, history =  magnitude_pruning(prune_epochs, train_dataset, test_dataset, schedule, model, seed = j)
        magnitude_models += [model]
        magnitude_histories += [history.history]
        with open('output/neural-network-pruning/pickle-jar/magnitude_histories'+str(j)+'.pickle', 'wb') as file:
            pickle.dump(magnitude_histories, file)


Epoch 1/200
235/235 [==============================] - 4s 15ms/step - loss: 2.1850 - accuracy: 0.9255 - val_loss: 1.5350 - val_accuracy: 0.9102
Epoch 2/200
235/235 [==============================] - 4s 16ms/step - loss: 0.4388 - accuracy: 0.9595 - val_loss: 0.4665 - val_accuracy: 0.9536
Epoch 3/200
235/235 [==============================] - 4s 15ms/step - loss: 0.3123 - accuracy: 0.9637 - val_loss: 0.3425 - val_accuracy: 0.9459
Epoch 4/200
235/235 [==============================] - 3s 15ms/step - loss: 0.2770 - accuracy: 0.9654 - val_loss: 0.3068 - val_accuracy: 0.9525
Epoch 5/200
235/235 [==============================] - 3s 13ms/step - loss: 0.2603 - accuracy: 0.9667 - val_loss: 0.2895 - val_accuracy: 0.9511
Epoch 6/200
235/235 [==============================] - 4s 15ms/step - loss: 0.2447 - accuracy: 0.9683 - val_loss: 0.2654 - val_accuracy: 0.9594
Epoch 7/200
235/235 [==============================] - 4s 15ms/step - loss: 0.2345 - accuracy: 0.9699 - val_loss: 0.2728 - val_accuracy:

235/235 [==============================] - 3s 14ms/step - loss: 0.1588 - accuracy: 0.9760 - val_loss: 0.1913 - val_accuracy: 0.9672
Epoch 58/200
235/235 [==============================] - 4s 16ms/step - loss: 0.1558 - accuracy: 0.9768 - val_loss: 0.2000 - val_accuracy: 0.9638
Epoch 59/200
235/235 [==============================] - 4s 15ms/step - loss: 0.1545 - accuracy: 0.9773 - val_loss: 0.2128 - val_accuracy: 0.9612
Epoch 60/200
235/235 [==============================] - 3s 15ms/step - loss: 0.1564 - accuracy: 0.9762 - val_loss: 0.2160 - val_accuracy: 0.9602
Epoch 61/200
235/235 [==============================] - 3s 15ms/step - loss: 0.1538 - accuracy: 0.9771 - val_loss: 0.2297 - val_accuracy: 0.9566
Epoch 62/200
235/235 [==============================] - 3s 15ms/step - loss: 0.1571 - accuracy: 0.9765 - val_loss: 0.2174 - val_accuracy: 0.9600
Epoch 63/200
235/235 [==============================] - 4s 15ms/step - loss: 0.1560 - accuracy: 0.9768 - val_loss: 0.2252 - val_accuracy: 0.956

235/235 [==============================] - 3s 14ms/step - loss: 0.1500 - accuracy: 0.9766 - val_loss: 0.2103 - val_accuracy: 0.9604
Epoch 114/200
235/235 [==============================] - 3s 15ms/step - loss: 0.1455 - accuracy: 0.9785 - val_loss: 0.2115 - val_accuracy: 0.9611
Epoch 115/200
235/235 [==============================] - 3s 14ms/step - loss: 0.1493 - accuracy: 0.9773 - val_loss: 0.2173 - val_accuracy: 0.9559
Epoch 116/200
235/235 [==============================] - 3s 14ms/step - loss: 0.1473 - accuracy: 0.9775 - val_loss: 0.2280 - val_accuracy: 0.9569
Epoch 117/200
235/235 [==============================] - 3s 14ms/step - loss: 0.1464 - accuracy: 0.9780 - val_loss: 0.2039 - val_accuracy: 0.9600
Epoch 118/200
235/235 [==============================] - 3s 15ms/step - loss: 0.1456 - accuracy: 0.9778 - val_loss: 0.2392 - val_accuracy: 0.9543
Epoch 119/200
235/235 [==============================] - 3s 15ms/step - loss: 0.1460 - accuracy: 0.9786 - val_loss: 0.2284 - val_accuracy:

235/235 [==============================] - 4s 15ms/step - loss: 0.1422 - accuracy: 0.9781 - val_loss: 0.2028 - val_accuracy: 0.9615
Epoch 170/200
235/235 [==============================] - 4s 15ms/step - loss: 0.1446 - accuracy: 0.9779 - val_loss: 0.2243 - val_accuracy: 0.9567
Epoch 171/200
235/235 [==============================] - 4s 15ms/step - loss: 0.1423 - accuracy: 0.9791 - val_loss: 0.1984 - val_accuracy: 0.9622
Epoch 172/200
235/235 [==============================] - 4s 15ms/step - loss: 0.1423 - accuracy: 0.9779 - val_loss: 0.1883 - val_accuracy: 0.9677
Epoch 173/200
235/235 [==============================] - 4s 15ms/step - loss: 0.1394 - accuracy: 0.9785 - val_loss: 0.1981 - val_accuracy: 0.9654
Epoch 174/200
235/235 [==============================] - 4s 15ms/step - loss: 0.1398 - accuracy: 0.9788 - val_loss: 0.2105 - val_accuracy: 0.9567
Epoch 175/200
235/235 [==============================] - 4s 15ms/step - loss: 0.1401 - accuracy: 0.9791 - val_loss: 0.2116 - val_accuracy:

235/235 [==============================] - 3s 15ms/step - loss: 5.2012e-04 - accuracy: 0.9999 - val_loss: 0.0698 - val_accuracy: 0.9838
Epoch 26/200
235/235 [==============================] - 4s 15ms/step - loss: 2.9209e-04 - accuracy: 1.0000 - val_loss: 0.0698 - val_accuracy: 0.9832
Epoch 27/200
235/235 [==============================] - 4s 15ms/step - loss: 1.8796e-04 - accuracy: 1.0000 - val_loss: 0.0701 - val_accuracy: 0.9834
Epoch 28/200
235/235 [==============================] - 4s 17ms/step - loss: 1.2218e-04 - accuracy: 1.0000 - val_loss: 0.0707 - val_accuracy: 0.9837
Epoch 29/200
235/235 [==============================] - 4s 17ms/step - loss: 1.0851e-04 - accuracy: 1.0000 - val_loss: 0.0709 - val_accuracy: 0.9834
Epoch 30/200
235/235 [==============================] - 4s 15ms/step - loss: 1.1920e-04 - accuracy: 1.0000 - val_loss: 0.0707 - val_accuracy: 0.9839
Epoch 31/200
235/235 [==============================] - 4s 15ms/step - loss: 7.7386e-05 - accuracy: 1.0000 - val_loss: 

...

235/235 [==============================] - 2s 9ms/step - loss: 0.5141 - accuracy: 0.8349 - val_loss: 0.5198 - val_accuracy: 0.8371
[ 0.  0.  0. ...  0. -0.  0.]
Sparsity at: 0.9718515289699571
Epoch 318/500
235/235 [==============================] - 2s 9ms/step - loss: 0.5112 - accuracy: 0.8360 - val_loss: 0.5171 - val_accuracy: 0.8383
[ 0.  0.  0. ...  0. -0.  0.]
Sparsity at: 0.9718515289699571
Epoch 319/500
235/235 [==============================] - 2s 9ms/step - loss: 0.5085 - accuracy: 0.8371 - val_loss: 0.5144 - val_accuracy: 0.8391
[ 0.  0.  0. ...  0. -0.  0.]
Sparsity at: 0.9718515289699571
Epoch 320/500
235/235 [==============================] - 2s 8ms/step - loss: 0.5061 - accuracy: 0.8376 - val_loss: 0.5119 - val_accuracy: 0.8403
[ 0.  0.  0. ...  0. -0.  0.]
Sparsity at: 0.9718515289699571
Epoch 321/500
235/235 [==============================] - 2s 8ms/step - loss: 0.5037 - accuracy: 0.8386 - val_loss: 0.5095 - val_accuracy: 0.8409
[ 0.  0.  0. ...  0. -0.  0.]
Sparsity at

[ 0.  0.  0. ... -0.  0.  0.]
Sparsity at: 0.9846097103004292
Epoch 357/500
235/235 [==============================] - 2s 8ms/step - loss: 1.3182 - accuracy: 0.5538 - val_loss: 1.2992 - val_accuracy: 0.5625
[ 0.  0.  0. ... -0.  0.  0.]
Sparsity at: 0.9846097103004292
Epoch 358/500
235/235 [==============================] - 2s 9ms/step - loss: 1.3155 - accuracy: 0.5547 - val_loss: 1.2971 - val_accuracy: 0.5637
[ 0.  0.  0. ... -0.  0.  0.]
Sparsity at: 0.9846097103004292
Epoch 359/500
235/235 [==============================] - 2s 8ms/step - loss: 1.3132 - accuracy: 0.5550 - val_loss: 1.2954 - val_accuracy: 0.5638
[ 0.  0.  0. ... -0.  0.  0.]
Sparsity at: 0.9846097103004292
Epoch 360/500
235/235 [==============================] - 2s 8ms/step - loss: 1.3113 - accuracy: 0.5558 - val_loss: 1.2939 - val_accuracy: 0.5644
[ 0.  0.  0. ... -0.  0.  0.]
Sparsity at: 0.9846097103004292
Epoch 361/500
235/235 [==============================] - 2s 9ms/step - loss: 1.3096 - accuracy: 0.5566 - val_l

235/235 [==============================] - 2s 7ms/step - loss: 1.2918 - accuracy: 0.5638 - val_loss: 1.2800 - val_accuracy: 0.5709
[ 0.  0.  0. ... -0.  0.  0.]
Sparsity at: 0.9846097103004292
Epoch 397/500
235/235 [==============================] - 2s 7ms/step - loss: 1.2915 - accuracy: 0.5638 - val_loss: 1.2798 - val_accuracy: 0.5710
[ 0.  0.  0. ... -0. -0.  0.]
Sparsity at: 0.9846097103004292
Epoch 398/500
235/235 [==============================] - 2s 7ms/step - loss: 1.2913 - accuracy: 0.5639 - val_loss: 1.2796 - val_accuracy: 0.5711
[ 0.  0.  0. ... -0.  0.  0.]
Sparsity at: 0.9846097103004292
Epoch 399/500
235/235 [==============================] - 2s 7ms/step - loss: 1.2911 - accuracy: 0.5639 - val_loss: 1.2795 - val_accuracy: 0.5712
[ 0.  0.  0. ... -0. -0.  0.]
Sparsity at: 0.9846097103004292
Epoch 400/500
235/235 [==============================] - 2s 7ms/step - loss: 1.2908 - accuracy: 0.5640 - val_loss: 1.2793 - val_accuracy: 0.5711
[ 0.  0.  0. ... -0.  0.  0.]
Sparsity at

[ 0.  0.  0. ... -0.  0. -0.]
Sparsity at: 0.9893374463519313
Epoch 436/500
235/235 [==============================] - 2s 9ms/step - loss: 1.5237 - accuracy: 0.4379 - val_loss: 1.5196 - val_accuracy: 0.4406
[ 0.  0.  0. ... -0. -0. -0.]
Sparsity at: 0.9893374463519313
Epoch 437/500
235/235 [==============================] - 2s 9ms/step - loss: 1.5236 - accuracy: 0.4379 - val_loss: 1.5195 - val_accuracy: 0.4406
[ 0.  0.  0. ... -0.  0. -0.]
Sparsity at: 0.9893374463519313
Epoch 438/500
235/235 [==============================] - 2s 8ms/step - loss: 1.5235 - accuracy: 0.4380 - val_loss: 1.5194 - val_accuracy: 0.4406
[ 0.  0.  0. ... -0. -0. -0.]
Sparsity at: 0.9893374463519313
Epoch 439/500
235/235 [==============================] - 2s 8ms/step - loss: 1.5234 - accuracy: 0.4378 - val_loss: 1.5193 - val_accuracy: 0.4406
[ 0.  0.  0. ... -0.  0. -0.]
Sparsity at: 0.9893374463519313
Epoch 440/500
235/235 [==============================] - 2s 9ms/step - loss: 1.5233 - accuracy: 0.4381 - val_l

235/235 [==============================] - 2s 9ms/step - loss: 1.5215 - accuracy: 0.4387 - val_loss: 1.5178 - val_accuracy: 0.4437
[ 0.  0.  0. ... -0. -0. -0.]
Sparsity at: 0.9893374463519313
Epoch 476/500
235/235 [==============================] - 2s 8ms/step - loss: 1.5215 - accuracy: 0.4388 - val_loss: 1.5177 - val_accuracy: 0.4419
[ 0.  0.  0. ... -0. -0. -0.]
Sparsity at: 0.9893374463519313
Epoch 477/500
235/235 [==============================] - 2s 9ms/step - loss: 1.5215 - accuracy: 0.4385 - val_loss: 1.5177 - val_accuracy: 0.4438
[ 0.  0.  0. ... -0.  0. -0.]
Sparsity at: 0.9893374463519313
Epoch 478/500
235/235 [==============================] - 2s 9ms/step - loss: 1.5215 - accuracy: 0.4387 - val_loss: 1.5177 - val_accuracy: 0.4438
[ 0.  0.  0. ... -0.  0. -0.]
Sparsity at: 0.9893374463519313
Epoch 479/500
235/235 [==============================] - 2s 9ms/step - loss: 1.5214 - accuracy: 0.4388 - val_loss: 1.5177 - val_accuracy: 0.4436
[ 0.  0.  0. ... -0.  0. -0.]
Sparsity at

In [14]:
magnitude_histories

[{'loss': [0.14014440774917603,
   0.138456791639328,
   0.13561511039733887,
   0.1380135416984558,
   0.13965007662773132,
   0.1374390423297882,
   0.13767531514167786,
   0.1386498063802719,
   0.1362529993057251,
   0.1350700557231903,
   0.1377331018447876,
   0.13773077726364136,
   0.13768739998340607,
   0.13749973475933075,
   0.13764218986034393,
   0.13913868367671967,
   0.13795582950115204,
   0.14177820086479187,
   0.13980919122695923,
   0.13669465482234955,
   0.1373773217201233,
   0.13808193802833557,
   0.14298556745052338,
   0.1391623467206955,
   0.13929204642772675,
   0.13684171438217163,
   0.13644978404045105,
   0.141718327999115,
   0.13884052634239197,
   0.1392638087272644,
   0.1366143375635147,
   0.13933834433555603,
   0.13659615814685822,
   0.13835333287715912,
   0.13728883862495422,
   0.13619688153266907,
   0.13964490592479706,
   0.13763608038425446,
   0.13871824741363525,
   0.13570727407932281,
   0.136813223361969,
   0.13998593389987946,


In [ ]:
with open('output/neural-network-pruning/pickle-jar/magnitude_histories'+str(j)+'.pickle', 'wb') as file:
            pickle.dump(magnitude_histories, file)